# Tracking through the map of a magnetic field
We want to transport a bunch of Carbon ions through the realistic field map of a strongly bent dipole magnet.

In [ ]:
%plot -f SVG

In [ ]:
RF_Track;

In [ ]:
addpath('scripts/')

## Define the key parameters
In the function ```init_ion```, we specify the key parameters of the reference particle.

In [ ]:
ion = init_ion()

## Let's create a bunch
This is a test bunch, with arbitrary Twiss parameters

In [ ]:
Twiss = Bunch6d_twiss();
Twiss.beta_x = 1; % m
Twiss.beta_y = 1; % m
Twiss.emitt_x = 1; % mm.mrad, normalised emittance 
Twiss.emitt_y = 1; % mm.mrad
Twiss.sigma_t = 1; % mm/c
Twiss.sigma_pt = 1; % permille, normalised energy spread
Twiss.disp_x = 0; % m, initial dispersion

In [ ]:
N_particles = 1000;

B0 = Bunch6d_QR (ion.mass, 0.0, ion.Z, ion.P_ref, Twiss, N_particles);

## Let's load the field map

In [ ]:
function V = init_volume()
    RF_Track;

    % Load field map from disk
    load('data/Dipole_Fieldmap.dat.gz');

    % Create RF-Track element
    S = Static_Magnetic_FieldMap (Bx, ... % T
                                  By, ...
                                  Bz, ...
                                  x_min_mm/1e3, ...
                                  y_min_mm/1e3, ...
                                  hx/1e3, ...
                                  hy/1e3, ...
                                  hz/1e3);

    % Init Volume
    V = Volume();
    V.add_ref(S, 0, 0, 0, 'center');
    
    V.odeint_algorithm = 'rk2';
    V.odeint_epsabs = 1e-8;
    V.cfx_dt_mm = 10;
    V.dt_mm = 0.1; % mm/c
    
    # Define the reference particle
    ion = init_ion ();
    P0 = Bunch6dT (ion.mass, 0, ion.Z, [ 0 0 0 0 0 ion.P_ref ]);

    % Set boudaries
    traj_len = 700; % mm
    t_mm = traj_len / ion.V_ref; % [mm/c]
    V.set_s0(0.0);
    V.set_s1(P0, t_mm);

endfunction

We can initialize the volume now

In [ ]:
V = init_volume();

## Let's plot the field
Using get_field over the plane $XZ$

In [ ]:
Xa = linspace(-150, 150, 101); % mm
Za = linspace(-700, 700, 201); % mm

%% XZ Plane
[X,Z] = meshgrid(Xa, Za);

[E,B] = V.get_field(X(:), 0, Z(:), 0);

Bx = reshape(B(:,1), size(X));
By = reshape(B(:,2), size(X));
Bz = reshape(B(:,3), size(X));

Here we plot it

In [ ]:
figure;
pcolor(Za, Xa, By');
h = colorbar;
shading flat
xlabel('z [mm]')
ylabel('x [mm]')
ylabel (h, 'B_y [T]');

## Let's perform tracking
We perform tracking in Lattice, to ease integration with downstream beamline elements

In [ ]:
V.set_tt_nsteps(10);

L = Lattice();
L.append_ref(V);

tic
B1 = L.track(B0);
toc

Let's retrieve the phase space and the transport table

In [ ]:
I1 = B1.get_phase_space('%x %Px %y %Py %t %E');

TT = L.get_transport_table('%S %beta_x %beta_y %disp_x %disp_px %emitt_x %emitt_y %emitt_4d %emitt_6d');

## Let's do some plots

In [ ]:
figure;
hold on
plot(TT(:,1), TT(:,2), 'displayname', 'beta_x', 'linewidth', 2);
plot(TT(:,1), TT(:,3), 'displayname', 'beta_y', 'linewidth', 2);
legend('location', 'northwest');
xlabel('S [m]')
ylabel('beta function [m]');

In [ ]:
figure;
hold on
plot(TT(:,1), TT(:,6), 'displayname', 'emitt_x', 'linewidth', 2);
plot(TT(:,1), TT(:,7), 'displayname', 'emitt_y', 'linewidth', 2);
legend('location', 'northwest');
xlabel('S [m]')
ylabel('normalised emittance [mm.mrad]');